## ELEX 4653 Final Exam

Instructions:

- Modify this notebook by adding the Python code described below.

- Test your code using the menu item `Cell  ► Run All` or `Run ► Run All Cells`

- Save the notebook (the .ipynb file) and upload it to the appropriate Assignment folder on the course web site.

#### Question 1

Write a function `modlist(l)` that returns 
a list containing strings equal to the strings in the list `l` converted to upper-case.

For example, `modlist(['yukin', 'dvzur', 'oexh', 'mj', 'lgin', 'eqyn'])` returns `['YUKIN', 'DVZUR', 'OEXH', 'MJ', 'LGIN', 'EQYN']`.


#### Question 2

Write a function `convert(l,s)` where `l` is a list and `s` is a set that returns
a list of strings in `l` with the strings that appear in `s` converted to upper-case. For example,
`convert(['er', 'vmhi', 'sp', 'hs', 'ia', 'tzzak', 'fwqfr'], {'fwqfr', 'tuy', 'dga', 'sp'})` returns `['er', 'vmhi', 'SP', 'hs', 'ia', 'tzzak', 'FWQFR']`.

#### Question 3
Write a function `edit(s)` that returns a string consisting of the string `s`
with every second word converted to UPPER-CASE.
The words in `s` are separated by a single space.

For example, `edit('fe mk xyt hsw ufyli pl obebz')` returns `'fe MK xyt HSW ufyli PL obebz'`.

#### Question 4

Write a function `check(l,f)` that calls the function `f` with successive values from the list `l` 
and returns a list containing the strings `"Y"` if calling `f` raised an exception and `"N"` otherwise

For example, if `f` is defined as:
```
def f(x):
    return 1/x
```
then `check([0, 1, 1, 0, 0, 1],f)` would return `['Y', 'N', 'N', 'Y', 'Y', 'N']`.

In [30]:
# lab validation code; do not modify
def labcheck(testing=0,ntest=10):
    '''
    Python exercise checking.
    Ed.Casas 2023-5-22
    Calls functions q<n>* and checks HMAC of return value[0].
    On mismatch prints return value[1] (function, arguments and return values).
    Setting testing=1 prints HMACs of correct results; paste into 'hashvalues'.
    Note:
    If q<n>* result not JSON-able, convert to string.
    Result order matters for comparison. Sort result if ordering not important.
    '''
    
    import base64, copy, hashlib, json, random, re, string, types 
    from random import randint
    import traceback
        
    # list of n words with nl letters from chars without repeats
    def randwords(n,chars=string.ascii_lowercase,nl=(2,5)):
        l = []
        while len(l)<n:
            w = ''.join([chars[randint(0,len(chars)-1)] for i in range(randint(*nl))])
            if w not in l:
                l.append(w)
        return l
        
    # convert sets to dicts and dict keys to strings so they can be sorted
    def orderkeys(o):
        if isinstance(o,set):
            return {str(k):None for k in o}
        if isinstance(o,dict):
            return {str(k):orderkeys(v) for k,v in o.items()}
        return o

    import math
    def roundn(num, n):
        return 0 if not num else round(num, -int(math.floor(math.log10(abs(num)))) + (n - 1))

    def ch(s,n=(1,1)):
        return randwords(1,chars=s,nl=n)[0]

    import ast, inspect
    def uses(f,s):
        for t in ast.walk(ast.parse(inspect.getsource(f))):
            if isinstance(t, ast.Call):
                if isinstance(t.func, ast.Name) and t.func.id == s:
                    return True
        return False
    
    class notalist(list):
        def __getitem__(self, index):
            raise TypeError("Indexing is not allowed, use the iterator.")

    def Q(f,*a,rounding=None):
        oa = copy.deepcopy(a)
        r = f(*a)
        r = roundn(r,rounding) if rounding else r
        return (r,f"{f.__name__}{repr(oa)} returns {repr(r)}")

    def Q1():
        return Q(modlist,randwords(randint(5,8)))
    
    def Q2():
        l = randwords(randint(5,7))
        s = set(l[:randint(2,3)]+randwords(2))
        random.shuffle(l)
        return Q(convert,l,s)
    
    def Q3():
        return Q(edit,' '.join(randwords(randint(5,8))))
    
    def Q4():
        def f(x):
            if randint(0,1):
                raise Exception
            else:
                pass
        return Q(check,[randint(0,2) for i in range(randint(5,8))],f)

    hashvalues = '''
F9ndaOSu6vju6u+u7M07IBCYt/xhWTjjtteP5ueJ
VeIBHowFhQv1jI0w07YLH/98dVW4cKpdL20CfknV
I0nnKQsmN3mI52KL7Yae8OjrMrNXO5ENCw53eyqP
4DPAtaUHo3mQdcouv97YeVRwlcZJb/Mbbmwb4c4y
'''.split()

    newhash = ''
    dsize = 3 # HMAC base64 digest size (bytes, use 3 or 6 for 4 or 8 char digests)
    dlen = ((dsize*8+5)//6+3)//4*4
           
    for n,f in [(n,f) for n,f in locals().items() if callable(f) and re.search(r'^[Qq]\d+.*',n)]:
        random.seed(n)      
        hashes = '0'*dlen*ntest if testing else hashvalues.pop(0)
        err = ''
        while hashes and not err:
            h, hashes = hashes[:dlen], hashes[dlen:] 
            try:
                v,s = f()
                b = json.dumps(orderkeys(v),sort_keys=True).encode()
                c = base64.b64encode(hashlib.blake2b(b,digest_size=dsize).digest()).decode()
                if testing:
                    print(s)
                    newhash += c
                else:
                    if c != h:
                        err = f"Wrong result for test {n}: {s} (HMAC={c} instead of {h})"
            except Exception as e:
                traceback.print_exc()
                err = f"Error during test {n}: {e}"               
        if testing:
           newhash += '\n'
        else:
            print(err or f"Passed test {n}.")
            
    if testing:
        print(newhash)

labcheck(0)